In [2]:
import pandas as pd
import numpy as np

train = pd.read_csv('../data/Etrain.csv')  # 导入训练集
test = pd.read_csv('../data/Etest.csv')  #导入测试集


In [3]:
#数值型和类别型分开处理
num_columns = []
cate_columns = []
for column in test.columns:
    if test.dtypes[column] != np.dtype('object'):
        num_columns.append(column)
    else:
        cate_columns.append(column)
print(num_columns)
print(cate_columns)

label = train.pop('SalePrice')

#缺失值填充
# 数值型用中值填充
for column in num_columns:
    train[column] = train[column].fillna(train[column].median())
    test[column] = test[column].fillna(test[column].median())

# # 类别型用最多的填充 
# for column in cate_columns:
#     train[column] = train[column].fillna(train[column].mode())
#     test[column] = test[column].fillna(test[column].mode())
    
# 类别型填充'NaN'
for column in cate_columns:
    train[column] = train[column].fillna('NaN')
    test[column] = test[column].fillna('NaN')
    
#类别型哑变量处理 将不能够定量处理的变量量化

data = pd.concat([train,test],axis=0) #训练集要和测试集放一起
for column in cate_columns:
    
    t = pd.get_dummies(data[column],prefix=column)
    train = pd.concat([train,t[:len(train)]],axis=1)
    train.drop(column,axis=1,inplace=True)
    
    test = pd.concat([test,t[len(train):]],axis=1)
    test.drop(column,axis=1,inplace=True)

['Id', 'OverallQual', 'YearBuilt', 'TotalBsmtSF', 'GrLivArea', 'FullBath', 'GarageCars']
['SaleType']


d:\environment\python\install\lib\site-packages\ipykernel_launcher.py:32: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



In [4]:
#回归
from sklearn.linear_model import Lasso,LinearRegression,Ridge,ElasticNet,TheilSenRegressor,HuberRegressor,RANSACRegressor
from sklearn.svm import SVR
from sklearn.tree import DecisionTreeRegressor,ExtraTreeRegressor
from sklearn.ensemble import AdaBoostRegressor,ExtraTreesRegressor,GradientBoostingRegressor,RandomForestRegressor
from xgboost import XGBRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import itertools

X_train, X_test, y_train, y_test = train_test_split(train, label, test_size=0.33, random_state=42)

regs = [
    ['Lasso',Lasso()],
    ['LinearRegression',LinearRegression()],
    ['Ridge',Ridge()],
    ['ElasticNet',ElasticNet()],
    ['TheilSenRegressor',TheilSenRegressor()],
    ['RANSACRegressor',RANSACRegressor()],
    ['HuberRegressor',HuberRegressor()],
    ['SVR',SVR(kernel='linear')],
    ['DecisionTreeRegressor',DecisionTreeRegressor()],
    ['ExtraTreeRegressor',ExtraTreeRegressor()],
    ['AdaBoostRegressor',AdaBoostRegressor(n_estimators=150)],
    ['ExtraTreesRegressor',ExtraTreesRegressor(n_estimators=150)],
    ['GradientBoostingRegressor',GradientBoostingRegressor(n_estimators=150)],
    ['RandomForestRegressor',RandomForestRegressor(n_estimators=150)],
    ['XGBRegressor',XGBRegressor(n_estimators=150)],
]

In [5]:
preds = []
for reg_name,reg in regs:
    print(reg_name)
    reg.fit(X_train,y_train)
    y_pred = reg.predict(X_test)
    if np.sum(y_pred<0) > 0:
        print('y_pred have',np.sum(y_pred<0),'negative values, we fill it with np.median(y_pred)')
        y_pred[y_pred<0] = np.median(y_pred)
    score = np.sqrt(mean_squared_error(np.log(y_test),np.log(y_pred)))
    preds.append([reg_name,y_pred])
    

final_results = []
for comb_length in range(1,len(regs)+1):
    print('Model Amount :',comb_length)
    results = []
    for comb in itertools.combinations(preds,comb_length):
        pred_sum = 0
        model_name = []
        for reg_name,pred in comb:
            pred_sum += pred
            model_name.append(reg_name)
        pred_sum /= comb_length
        model_name = '+'.join(model_name)
        score = np.sqrt(mean_squared_error(np.log(y_test),np.log(pred_sum)))
        results.append([model_name,score])
    results = sorted(results,key=lambda x:x[1])
    for model_name,score in results:
        print(model_name,score)
    print()
    final_results.append(results[0])

Lasso
y_pred have 1 negative values, we fill it with np.median(y_pred)
LinearRegression
y_pred have 1 negative values, we fill it with np.median(y_pred)
Ridge
y_pred have 1 negative values, we fill it with np.median(y_pred)
ElasticNet
TheilSenRegressor
RANSACRegressor
HuberRegressor
SVR
DecisionTreeRegressor
ExtraTreeRegressor
AdaBoostRegressor
ExtraTreesRegressor
GradientBoostingRegressor
RandomForestRegressor
XGBRegressor


d:\environment\python\install\lib\site-packages\xgboost\core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \


Model Amount : 1
RandomForestRegressor 0.164708312807971
XGBRegressor 0.16652750584015594
ExtraTreesRegressor 0.16865090473000927
GradientBoostingRegressor 0.1783677791198387
ElasticNet 0.1837951464056652
RANSACRegressor 0.19025631163408524
Ridge 0.1975075594882399
SVR 0.20208265769614225
HuberRegressor 0.20275104844900102
AdaBoostRegressor 0.20640573552149746
Lasso 0.21140993127755417
LinearRegression 0.2124312121467681
DecisionTreeRegressor 0.22394281740663602
ExtraTreeRegressor 0.22949163187862606
TheilSenRegressor 0.2853654695968851

Model Amount : 2
RandomForestRegressor+XGBRegressor 0.16240703935245435
ExtraTreesRegressor+XGBRegressor 0.16306983440677605
RANSACRegressor+RandomForestRegressor 0.16346082156939212
ElasticNet+RandomForestRegressor 0.16354320318661292
ElasticNet+ExtraTreesRegressor 0.16397138494206434
ExtraTreesRegressor+RandomForestRegressor 0.16461509215039496
RANSACRegressor+ExtraTreesRegressor 0.1646595004115629
ElasticNet+XGBRegressor 0.165412115180952
RANSACRegr

Lasso+RANSACRegressor+HuberRegressor 0.18314865253503815
LinearRegression+RANSACRegressor+HuberRegressor 0.18319456510241725
ElasticNet+RANSACRegressor+SVR 0.18341615091844365
Lasso+LinearRegression+DecisionTreeRegressor 0.18371211978453608
Lasso+Ridge+SVR 0.1837836678671334
LinearRegression+Ridge+SVR 0.18383951843220267
Lasso+Ridge+ExtraTreeRegressor 0.18472038562714377
LinearRegression+Ridge+ExtraTreeRegressor 0.18479409907763944
Lasso+LinearRegression+GradientBoostingRegressor 0.1852947920155535
ElasticNet+RANSACRegressor+HuberRegressor 0.18559178541472782
Lasso+LinearRegression+SVR 0.18575740358292922
Lasso+LinearRegression+ExtraTreeRegressor 0.18742798943515723
Lasso+Ridge+ElasticNet 0.18850669548283133
LinearRegression+Ridge+ElasticNet 0.18856734261092167
Lasso+Ridge+RANSACRegressor 0.18882497623476519
LinearRegression+Ridge+RANSACRegressor 0.18889858748160246
TheilSenRegressor+ExtraTreesRegressor+XGBRegressor 0.19069163621174387
Lasso+LinearRegression+ElasticNet 0.19072363920599

Lasso+LinearRegression+SVR+AdaBoostRegressor 0.1745605679157318
Lasso+LinearRegression+ElasticNet+RandomForestRegressor 0.1747099281780382
Lasso+LinearRegression+ExtraTreeRegressor+ExtraTreesRegressor 0.17471997206395307
Lasso+Ridge+ElasticNet+AdaBoostRegressor 0.17482586900630445
Lasso+LinearRegression+RANSACRegressor+RandomForestRegressor 0.17483173079616302
LinearRegression+Ridge+ElasticNet+AdaBoostRegressor 0.17485250536562572
Lasso+ElasticNet+HuberRegressor+ExtraTreeRegressor 0.17487680163829025
LinearRegression+ElasticNet+HuberRegressor+ExtraTreeRegressor 0.17489890697866975
Lasso+LinearRegression+RANSACRegressor+AdaBoostRegressor 0.1749459780357176
Lasso+RANSACRegressor+HuberRegressor+ExtraTreeRegressor 0.17498724584535372
LinearRegression+RANSACRegressor+HuberRegressor+ExtraTreeRegressor 0.1750142353853542
Lasso+Ridge+SVR+ExtraTreeRegressor 0.1750155818690584
LinearRegression+Ridge+SVR+ExtraTreeRegressor 0.17504881685908735
Lasso+LinearRegression+DecisionTreeRegressor+GradientB

...

Lasso+TheilSenRegressor+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.16769757642614683
LinearRegression+ElasticNet+TheilSenRegressor+RANSACRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+XGBRegressor 0.1676980225348338
LinearRegression+TheilSenRegressor+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.16769967222417073
Lasso+ElasticNet+TheilSenRegressor+RANSACRegressor+HuberRegressor+DecisionTreeRegressor+ExtraTreeRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.1677006712191084
LinearRegression+ElasticNet+TheilSenRegressor+RANSACRegressor+HuberRegressor+DecisionTreeRegressor+ExtraTreeRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.16770317360307047
Ridge+TheilSenRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoo

Lasso+LinearRegression+ElasticNet+TheilSenRegressor+SVR+AdaBoostRegressor+ExtraTreesRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.1702649100800902
Lasso+Ridge+ElasticNet+TheilSenRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+RandomForestRegressor 0.1702650723975693
LinearRegression+Ridge+ElasticNet+TheilSenRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+RandomForestRegressor 0.1702672973679694
Lasso+LinearRegression+Ridge+TheilSenRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+GradientBoostingRegressor 0.17026758373743547
Lasso+Ridge+TheilSenRegressor+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.17026839946831926
Lasso+Ridge+ElasticNet+TheilSenRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+XGBRegressor 0.1702698277560282


Lasso+Ridge+ElasticNet+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+RandomForestRegressor 0.1625996681816194
LinearRegression+Ridge+ElasticNet+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+XGBRegressor 0.16260477171265136
LinearRegression+Ridge+ElasticNet+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+RandomForestRegressor 0.16260487337483887
Lasso+Ridge+ElasticNet+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.16261096094777341
LinearRegression+Ridge+ElasticNet+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.16261653832888567
Lasso+Ridge+ElasticNet+RANSACRegressor+HuberRegressor+DecisionTreeRegressor+AdaBoostRegressor+

LinearRegression+Ridge+TheilSenRegressor+RANSACRegressor+HuberRegressor+SVR+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+GradientBoostingRegressor+RandomForestRegressor 0.16892532883458475
Lasso+LinearRegression+ElasticNet+TheilSenRegressor+RANSACRegressor+HuberRegressor+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+GradientBoostingRegressor+RandomForestRegressor 0.16893085106734604
Lasso+LinearRegression+Ridge+TheilSenRegressor+RANSACRegressor+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.16893691932185328
Lasso+Ridge+ElasticNet+TheilSenRegressor+RANSACRegressor+HuberRegressor+DecisionTreeRegressor+ExtraTreeRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.1689388577791198
LinearRegression+Ridge+ElasticNet+TheilSenRegressor+RANSACRegressor+HuberRegressor+DecisionTreeRegressor+ExtraTreeRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.168942

Ridge+ElasticNet+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.1610660945821524
Lasso+ElasticNet+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.16116276849374211
LinearRegression+ElasticNet+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.1611672872020393
Lasso+Ridge+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.16153362044257197
LinearRegression+Ridge+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+GradientBoo

In [6]:
final_results = sorted(final_results,key=lambda x:x[1])
for model_name,score in final_results:
    print(model_name,score)

RANSACRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.16040358128157686
Ridge+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.16082722048117293
Ridge+RANSACRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.16084851056535054
Ridge+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor+ExtraTreesRegressor+GradientBoostingRegressor+RandomForestRegressor+XGBRegressor 0.1609017028600026
Ridge+RANSACRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.16090492420027447
Ridge+RANSACRegressor+SVR+DecisionTreeRegressor+ExtraTreesRegressor+RandomForestRegressor+XGBRegressor 0.1610078954175915
Ridge+ElasticNet+RANSACRegressor+HuberRegressor+SVR+DecisionTreeRegressor+ExtraTreeRegressor+AdaBoostRegressor

In [ ]:
#最终输出
[b for b in zip(itertools.count(),[a[0] for a in regs])]

pred = np.mean(list(map(lambda x:regs[x][1].predict(test),[0,12,14])),axis=0)

sub = pd.DataFrame({'Id':test['Id'],'SalePrice':pred})
sub.to_csv('./NaN.csv',index=None)